# 📥 Pipeline de Ingestão CDC - Upcell

Este notebook implementa o pipeline de ingestão de dados CDC (Change Data Capture) do S3 para o Bronze no Databricks.

## 🎯 Objetivo
- **Full-load**: Carga inicial completa das tabelas
- **CDC**: Ingestão incremental com operações Insert, Update e Delete
- **Delta Lake**: Merge atômico na camada Bronze

## 📋 Requisitos
- Tabelas no S3: `s3://meudatalake-raw/upcell/`
- Catálogo: `bronze.upcell`
- Coluna de controle: `DtAtualizacao` (presente em todos os arquivos)

In [0]:
import delta

## 1️⃣ Importações e Setup

In [0]:
spark.catalog.clearCache()

In [0]:
# Teste: Visualizar arquivos CDC disponíveis
df_test = spark.read.format("parquet").load(f"/Volumes/raw/upcell/cdc/transacao_produto/")
print(f"Total de registros CDC: {df_test.count()}")
print(f"Colunas: {df_test.columns}")
display(df_test.limit(5))

idTransacaoProduto IdTransacao IdProduto QtdeProduto vlProduto op DtAtualizacao 0030d8a6-af29-47a9-96ab-2ef1b5d5668c deafb051-ff5b-4d63-ae30-490da938d2de 5 1 1 I 2025-10-03T16:37:34.807051 003b43ff-9ade-41c2-a1bc-fb54b21e09ea e125d9c5-614c-4688-b47d-0abc5fc3c363 5 1 1 I 2025-10-03T16:37:34.807051 0045ff13-09c2-41c2-8ddc-cb5181ace922 67e9fdbe-1935-40af-aad6-c26f3d6e015d 5 1 1 I 2025-10-03T16:37:34.807051 004b2ff9-7980-4cb3-be8c-ffbef2837106 bd4791ea-fc30-47d6-9b65-ea9d2f9c7a1f 5 1 1 I 2025-10-03T16:37:34.807051 00a10130-aaab-41a0-8f37-45d917ae5def e7855cb3-1efa-49a3-b1bd-cebdcb219813 5 1 1 I 2025-10-03T16:37:34.807051 00b93f8e-2a33-4a8c-bec4-a0882faffa09 24634e16-95cf-4cb0-ab0e-add1fadded12 5 1 1 I 2025-10-03T16:37:34.807051 0100f58e-c5ac-4ba1-a8ee-1871542e9014 238dd9f2-97d3-46b9-b71f-e04dec2e5548 11 1 50 I 2025-10-03T16:37:34.807051 0122a02d-f7ca-4470-96cd-d47b7588bf80 aabd7edd-a066-48d3-88d3-69b9dfb0d7c8 11 1 50 I 2025-10-03T16:37:34.807051 014b384b-39ca-40b8-88d1-dea2ae188a8f f1a7cec7-b143-465b-b6e7-5e07f36fab6c 11 1 50 I 2025-10-03T16:37:34.807051 016d8225-bd37-4490-9696-b1d7ec533c99 c38f4092-15d6-4614-817d-50eb5c10145c 5 1 1 I 2025-10-03T16:37:34.807051 01767c0b-650a-4394-9d77-ac12619f3620 0aae477d-3c40-49a2-8979-5234dc00d69e 5 1 1 I 2025-10-03T16:37:34.807051 01c85ea7-7acc-4ccd-9d58-43bba41fc6b3 55d90e41-44f6-4a84-bbfb-d26693c549bd 5 1 1 I 2025-10-03T16:37:34.807051 01f310f0-60cf-4bb1-a736-01ef59fbb741 1ceb9289-f8c4-4722-a617-45e21ab102ef 5 1 1 I 2025-10-03T16:37:34.807051 022acb5f-15be-4a4e-a1b7-5e34c0965a66 b054e6ea-d463-4180-93cc-60d1418af0d4 5 1 1 I 2025-10-03T16:37:34.807051 02429eb3-3e11-4cad-b373-437a0e91fa5b 339b8378-087b-4d37-b9ab-26783ac57553 5 1 1 I 2025-10-03T16:37:34.807051 02549885-403b-4418-a849-08d08733b0f4 b3efc806-b42a-4803-b39f-a934dd2bdf18 5 1 1 I 2025-10-03T16:37:34.807051 02595ecc-00ba-4205-b29a-85a11fe07c92 2e65faed-caaf-44aa-a795-daaeca6ef366 5 1 1 I 2025-10-03T16:37:34.807051 02614c40-6e8e-4e6a-902d-3d4ad05e253a e5974bdf-3e4b-4953-9c08-21291cc5e390 5 1 1 I 2025-10-03T16:37:34.807051 0278fb0d-2bf7-4820-b426-3c34769688ce 6f2ff6ba-d052-4e97-bf6c-d9d7d3afe95e 5 1 1 I 2025-10-03T16:37:34.807051 027f44f2-77ca-438c-bb81-bd824aa2dd96 3fabe804-de32-4963-ae42-1db09af0b192 5 1 1 I 2025-10-03T16:37:34.807051 02975538-09af-4630-8507-91fdafe23bac f454117b-39e1-4d29-9467-b6c84a2efd7a 5 1 1 I 2025-10-03T16:37:34.807051 0316ee1c-688d-4b4d-8a7f-7a3d745732e5 4ad8c3f9-020f-4353-9db3-09bac8efbf69 5 1 1 I 2025-10-03T16:37:34.807051 0328ec52-4f99-4963-823c-e96d948603bd 5084657f-d2d2-46ae-b17b-7e37b6abca19 5 1 1 I 2025-10-03T16:37:34.807051 0333d533-ce29-421a-bc82-3838ca563af9 2192f4e6-f8d3-4392-8a6f-23062268c652 5 1 1 I 2025-10-03T16:37:34.807051 0382bf7a-d3d1-4501-b995-f0dfc2d9b61a 0f49444e-38b8-4d2b-91e6-f02e58cfbad7 5 1 1 I 2025-10-03T16:37:34.807051 0394172d-7692-4468-b7d7-f43f9be70db6 5b08d346-90e0-4069-bdd7-e63b27cb0ca9 5 1 1 I 2025-10-03T16:37:34.807051 03af92a0-ec89-4405-8069-3e0f90332a63 9cff802a-1065-4504-888a-89752c7ce66f 5 1 1 I 2025-10-03T16:37:34.807051 03e8a6bd-7a3e-4985-b7ec-27517a164feb 2157a02c-a18f-43fa-9e1d-48a1fe3e632b 5 1 1 I 2025-10-03T16:37:34.807051 040f642e-a2e5-4085-8879-92d7ab2c26b2 cdb8f6c4-78b3-4bf0-825f-efda4fe735c4 5 1 1 I 2025-10-03T16:37:34.807051 04a67064-1f01-45c7-931c-1239a7c1d259 ad1e6f05-d6bd-456f-86cf-3bb2c9527fee 5 1 1 I 2025-10-03T16:37:34.807051 04b8826a-9e53-4064-a001-4affd102e247 b62e372b-3af2-4491-a0df-a025f509e534 5 1 1 I 2025-10-03T16:37:34.807051 04bb4bd8-7c65-472b-a496-77b242a5e488 3b521122-a0d9-4cc2-80a6-a133890deb9c 5 1 1 I 2025-10-03T16:37:34.807051 04bd1ca5-f830-4bcd-8dfd-35c3e2b4fccd b7370d23-7b30-4d64-a8db-15e49b09091d 5 1 1 I 2025-10-03T16:37:34.807051 04e9da41-66ae-4983-bbaa-22648adfd329 4692c510-4cf2-4f19-ac62-144252c97b34 5 1 1 I 2025-10-03T16:37:34.807051 04f8dea5-6023-4886-bfd2-45accdadb6c1 0c83ac5a-7d89-43bc-8208-15e716da7c2b 5 1 1 I 2025-10-03T16:37:34.807051 050e93e7-e8b2-49fa-a3a6-508a02fd76f8 8d66e6e2-1650-4284-bae3-296dfece54da 5 1 1 I 2025-10-03T16:37:

In [0]:
def table_exists(catalog, database, table):
    count = (spark.sql(f"SHOW TABLES IN `{catalog}`.`{database}`")
               .filter(f"database = '{database}' AND tableName = '{table}'")
               .count())
    return count == 1

In [0]:
catalog = "bronze"
schema = "upcell"
tablename = "transacao_produto"
id_field = "idTransacaoProduto"
timefield = "DtAtualizacao"

## 2️⃣ Configuração da Tabela

Defina a tabela que será processada e os campos de controle.

In [0]:
# Carga inicial: Cria tabela Delta a partir do full-load
if not table_exists(catalog, schema, tablename):
    print(f"⚠️  Tabela {catalog}.{schema}.{tablename} NÃO existe. Criando a partir do full-load...")

    # Lê full-load (já tem DtAtualizacao!)
    df_full = spark.read.format("parquet").load(f"/Volumes/raw/upcell/full-load/{tablename}")
    
    print(f"📊 Total de registros no full-load: {df_full.count():,}")

    # Cria tabela Delta
    (df_full.coalesce(1)
            .write
            .format("delta")
            .mode("overwrite")
            .saveAsTable(f"{catalog}.{schema}.{tablename}"))
    
    print(f"✅ Tabela {catalog}.{schema}.{tablename} criada com sucesso!")
    
else:
    print(f"✅ Tabela {catalog}.{schema}.{tablename} já existe. Pular para o CDC merge.")

tabela nao existe, criando....


## 3️⃣ Full-Load (Carga Inicial)

Se a tabela não existe, cria a partir dos dados de full-load.

In [0]:
%sql
select * from bronze.upcell.transacoes

IdTransacao IdCliente DtCriacao QtdePontos DescSistemaOrigem DtAtualizacao 0000520a-a4e5-4977-b360-17be62fa0f2b 24782f0b-4683-4f35-976a-ea21d6714ba6 2025-09-17 12:28:41.864 1 twitch 2025-10-03T17:05:11.008701 000060e8-aa76-4286-a8d7-f30e6fa47edd 252a0923-3f79-45bb-b664-3040235c6c58 2024-07-23 12:49:49.874 1 twitch 2025-10-03T17:05:11.008701 000095de-3daa-4cfb-a0ae-e7b2c8bc3c9b 30f45a6d-ada5-4a17-8338-710e414eb6c6 2025-09-17 13:38:57.479 1 twitch 2025-10-03T17:05:11.008701 0000c010-a592-46f7-8b0b-6f841bee64ba 65662aff-44d6-4f06-b9d9-07445c6e5943 2025-10-03 12:23:39.779 1 twitch 2025-10-03T17:05:11.008701 0000dfbb-e14e-4ea7-a57f-60236869fffe 5f8fcbe0-6014-43f8-8b83-38cf2f4887b3 2024-02-20 13:21:45.613 1 twitch 2025-10-03T17:05:11.008701 0000e94f-fb76-42b7-82e3-5059b6e40703 3884c92f-a635-4b67-9e5a-97730829cdca 2024-02-05 13:27:18.987 1 twitch 2025-10-03T17:05:11.008701 00017768-81eb-45ae-ad56-f189dd657808 3b878853-34a5-44be-9a8e-05642b853dc6 2025-09-30 12:02:16.448 1 twitch 2025-10-03T17:05:11.008701 00019b46-6b25-47c3-aa8f-f550d7dbcb00 e2624c1c-c8af-4622-94e0-f3470037292f 2024-06-20 19:22:45.600 1 twitch 2025-10-03T17:05:11.008701 0001d503-58d0-4c3e-b0f4-eda1d5f97d06 9aba2685-7c0a-4d1f-8e22-0c47ca0af580 2024-03-18 13:04:21.814 1 twitch 2025-10-03T17:05:11.008701 0001fa55-581a-44e6-8e40-1bb44f82de8e 05de679b-9989-4416-9aa4-20c149999c8d 2024-07-11 13:46:05.759 1 twitch 2025-10-03T17:05:11.008701 000219b4-75c8-4c76-8752-56eaf744bbe0 4fade907-6e0f-4581-a674-aad6622b1b10 2024-08-30 13:43:05.591 1 twitch 2025-10-03T17:05:11.008701 00028d36-4575-4d02-b2a0-bdae1bc83231 9d023e72-c799-40c0-907a-96e023a97959 2024-11-11 12:36:33.625 50 twitch 2025-10-03T17:05:11.008701 00028f94-1cf3-413c-91dd-652dc1a9e161 5f8fcbe0-6014-43f8-8b83-38cf2f4887b3 2024-02-05 11:54:38.711 1 twitch 2025-10-03T17:05:11.008701 00029103-193c-4c63-9cc6-f6f3fbbfbd51 f19aaa00-f337-4174-ba14-a2a39dd6ebbf 2025-09-18 12:02:03.817 1 twitch 2025-10-03T17:05:11.008701 0002df88-1e1f-47b9-8cd4-8f36f21a36c9 b9d0832d-31e7-4031-b548-b060947cde94 2024-08-19 13:43:13.613 1 twitch 2025-10-03T17:05:11.008701 00030a97-75d6-4d58-b0ca-96d4228dc22c 5f8fcbe0-6014-43f8-8b83-38cf2f4887b3 2024-04-20 00:30:59.648 1 twitch 2025-10-03T17:05:11.008701 00030cf7-7a2b-42ab-bbc9-a1642c4cc8c4 700ea785-2faf-4d64-84ea-4e19dc209b56 2025-08-25 13:46:48.572 1 twitch 2025-10-03T17:05:11.008701 000331ee-8fbf-4a2b-a963-6ffd2b86e66a 24782f0b-4683-4f35-976a-ea21d6714ba6 2024-09-04 12:08:52.226 1 twitch 2025-10-03T17:05:11.008701 00033b0f-f658-456c-ab77-e5b40396a2f3 056caf66-d67b-449e-8cba-0bab8aca5949 2025-08-11 12:28:50.404 1 twitch 2025-10-03T17:05:11.008701 00037782-0a3c-4a28-9bd4-564dafec1fca 1856963a-84cb-453e-a139-eb7d8d9b3255 2025-02-19 12:36:18.928 1 twitch 2025-10-03T17:05:11.008701 0003b91b-a75a-46e5-8af6-fcc890b98952 5877cf53-bde0-4bfa-b61b-0a09e5dd5147 2024-01-30 13:17:36.457 1 twitch 2025-10-03T17:05:11.008701 00045cfe-f131-4505-ba34-d89f099a8625 69e9a7c3-6f64-430f-96ee-eb1548eb6aad 2024-02-05 13:35:41.807 1 twitch 2025-10-03T17:05:11.008701 0004bd85-fe2c-4b39-a7f0-1a05b009011a da98830d-a2d1-4c15-801d-dd58ef7713fb 2025-10-01 13:37:39.603 1 twitch 2025-10-03T17:05:11.008701 0004da1b-ab20-4460-9106-3aeca2844789 5f8fcbe0-6014-43f8-8b83-38cf2f4887b3 2025-09-02 12:00:52.769 1 twitch 2025-10-03T17:05:11.008701 0005255f-3ab1-4052-a0d5-0f71a87e492e d6ae3f9a-f285-4a55-9888-9e950a775b76 2025-03-18 11:10:11.890 1 twitch 2025-10-03T17:05:11.008701 0005855d-2c33-4bfd-85fe-2c7ffaf73151 f5719706-915b-4bb1-b9be-c4acb3bd7837 2025-07-16 12:05:28.007 50 twitch 2025-10-03T17:05:11.008701 0005df42-fa29-418e-8da8-cf60ed680a28 c4c318f5-16b8-4c4f-b830-56d6e79f458e 2024-11-19 11:40:09.911 1 twitch 2025-10-03T17:05:11.008701 000649f4-446e-4c61-b527-50db534ab6fb 8d86f053-91ab-44ed-aeb8-74cad60760b8 2025-04-24 13:13:21.114 1 twitch 2025-10-03T17:05:11.008701 00068684-c433-45e1-ae95-a6b94cbeb514 961622c3-3c29-4fa1-88d2-4f408d6d6ebb 2024-08-09 13:14:40.064 1 twitch 2025-10-03T17:05:11.008701 00068e23-5b1e-432a-83df-8a5d11e495a6 

In [0]:
# Processa CDC: Filtra apenas arquivos novos e deduplica
print("📥 Carregando dados CDC...")

# 1. Busca a última atualização já processada na tabela Bronze
last_processed = spark.sql(f"""
    SELECT COALESCE(MAX(DtAtualizacao), '1900-01-01') as last_dt
    FROM {catalog}.{schema}.{tablename}
""").collect()[0]['last_dt']

print(f"? Última atualização processada: {last_processed}")

# 2. Lê TODOS os arquivos CDC (por enquanto)
(spark.read
    .format("parquet")
    .load(f"/Volumes/raw/upcell/cdc/{tablename}")
    .createOrReplaceTempView(f"view_{tablename}"))

# 3. Filtra apenas registros NOVOS (DtAtualizacao > última processada)
query_filter = f"""
    SELECT *  
    FROM view_{tablename}
    WHERE DtAtualizacao > '{last_processed}'
"""

df_cdc_new = spark.sql(query_filter)
total_new_records = df_cdc_new.count()

print(f"📊 Total de registros CDC NOVOS: {total_new_records:,}")

if total_new_records == 0:
    print("⚠️  Nenhum registro CDC novo encontrado. Pulando merge.")
    df_cdc_unique = df_cdc_new  # DataFrame vazio
else:
    # 4. Deduplica: Pega apenas o último registro de cada chave (nos dados NOVOS)
    query_dedupe = f"""
        SELECT *  
        FROM view_{tablename}
        WHERE DtAtualizacao > '{last_processed}'
        QUALIFY ROW_NUMBER() OVER(PARTITION BY {id_field} ORDER BY {timefield} DESC) = 1
    """
    
    df_cdc_unique = spark.sql(query_dedupe)
    
    print(f"📊 Total de registros CDC únicos (após deduplicação): {df_cdc_unique.count():,}")
    print(f"📋 Operações no CDC:")
    df_cdc_unique.groupBy("op").count().display()
    
    print("\n🔍 Sample de registros CDC:")
    df_cdc_unique.display()

idTransacaoProduto IdTransacao IdProduto QtdeProduto vlProduto op DtAtualizacao 0030d8a6-af29-47a9-96ab-2ef1b5d5668c deafb051-ff5b-4d63-ae30-490da938d2de 5 1 1 I 2025-10-03T16:37:34.807051 003b43ff-9ade-41c2-a1bc-fb54b21e09ea e125d9c5-614c-4688-b47d-0abc5fc3c363 5 1 1 I 2025-10-03T16:37:34.807051 0045ff13-09c2-41c2-8ddc-cb5181ace922 67e9fdbe-1935-40af-aad6-c26f3d6e015d 5 1 1 I 2025-10-03T16:37:34.807051 004b2ff9-7980-4cb3-be8c-ffbef2837106 bd4791ea-fc30-47d6-9b65-ea9d2f9c7a1f 5 1 1 I 2025-10-03T16:37:34.807051 00a10130-aaab-41a0-8f37-45d917ae5def e7855cb3-1efa-49a3-b1bd-cebdcb219813 5 1 1 I 2025-10-03T16:37:34.807051 00b93f8e-2a33-4a8c-bec4-a0882faffa09 24634e16-95cf-4cb0-ab0e-add1fadded12 5 1 1 I 2025-10-03T16:37:34.807051 0100f58e-c5ac-4ba1-a8ee-1871542e9014 238dd9f2-97d3-46b9-b71f-e04dec2e5548 11 1 50 I 2025-10-03T16:37:34.807051 0122a02d-f7ca-4470-96cd-d47b7588bf80 aabd7edd-a066-48d3-88d3-69b9dfb0d7c8 11 1 50 I 2025-10-03T16:37:34.807051 014b384b-39ca-40b8-88d1-dea2ae188a8f f1a7cec7-b143-465b-b6e7-5e07f36fab6c 11 1 50 I 2025-10-03T16:37:34.807051 016d8225-bd37-4490-9696-b1d7ec533c99 c38f4092-15d6-4614-817d-50eb5c10145c 5 1 1 I 2025-10-03T16:37:34.807051 01767c0b-650a-4394-9d77-ac12619f3620 0aae477d-3c40-49a2-8979-5234dc00d69e 5 1 1 I 2025-10-03T16:37:34.807051 01c85ea7-7acc-4ccd-9d58-43bba41fc6b3 55d90e41-44f6-4a84-bbfb-d26693c549bd 5 1 1 I 2025-10-03T16:37:34.807051 01f310f0-60cf-4bb1-a736-01ef59fbb741 1ceb9289-f8c4-4722-a617-45e21ab102ef 5 1 1 I 2025-10-03T16:37:34.807051 022acb5f-15be-4a4e-a1b7-5e34c0965a66 b054e6ea-d463-4180-93cc-60d1418af0d4 5 1 1 I 2025-10-03T16:37:34.807051 02429eb3-3e11-4cad-b373-437a0e91fa5b 339b8378-087b-4d37-b9ab-26783ac57553 5 1 1 I 2025-10-03T16:37:34.807051 02549885-403b-4418-a849-08d08733b0f4 b3efc806-b42a-4803-b39f-a934dd2bdf18 5 1 1 I 2025-10-03T16:37:34.807051 02595ecc-00ba-4205-b29a-85a11fe07c92 2e65faed-caaf-44aa-a795-daaeca6ef366 5 1 1 I 2025-10-03T16:37:34.807051 02614c40-6e8e-4e6a-902d-3d4ad05e253a e5974bdf-3e4b-4953-9c08-21291cc5e390 5 1 1 I 2025-10-03T16:37:34.807051 0278fb0d-2bf7-4820-b426-3c34769688ce 6f2ff6ba-d052-4e97-bf6c-d9d7d3afe95e 5 1 1 I 2025-10-03T16:37:34.807051 027f44f2-77ca-438c-bb81-bd824aa2dd96 3fabe804-de32-4963-ae42-1db09af0b192 5 1 1 I 2025-10-03T16:37:34.807051 02975538-09af-4630-8507-91fdafe23bac f454117b-39e1-4d29-9467-b6c84a2efd7a 5 1 1 I 2025-10-03T16:37:34.807051 0316ee1c-688d-4b4d-8a7f-7a3d745732e5 4ad8c3f9-020f-4353-9db3-09bac8efbf69 5 1 1 I 2025-10-03T16:37:34.807051 0328ec52-4f99-4963-823c-e96d948603bd 5084657f-d2d2-46ae-b17b-7e37b6abca19 5 1 1 I 2025-10-03T16:37:34.807051 0333d533-ce29-421a-bc82-3838ca563af9 2192f4e6-f8d3-4392-8a6f-23062268c652 5 1 1 I 2025-10-03T16:37:34.807051 0382bf7a-d3d1-4501-b995-f0dfc2d9b61a 0f49444e-38b8-4d2b-91e6-f02e58cfbad7 5 1 1 I 2025-10-03T16:37:34.807051 0394172d-7692-4468-b7d7-f43f9be70db6 5b08d346-90e0-4069-bdd7-e63b27cb0ca9 5 1 1 I 2025-10-03T16:37:34.807051 03af92a0-ec89-4405-8069-3e0f90332a63 9cff802a-1065-4504-888a-89752c7ce66f 5 1 1 I 2025-10-03T16:37:34.807051 03e8a6bd-7a3e-4985-b7ec-27517a164feb 2157a02c-a18f-43fa-9e1d-48a1fe3e632b 5 1 1 I 2025-10-03T16:37:34.807051 040f642e-a2e5-4085-8879-92d7ab2c26b2 cdb8f6c4-78b3-4bf0-825f-efda4fe735c4 5 1 1 I 2025-10-03T16:37:34.807051 04a67064-1f01-45c7-931c-1239a7c1d259 ad1e6f05-d6bd-456f-86cf-3bb2c9527fee 5 1 1 I 2025-10-03T16:37:34.807051 04b8826a-9e53-4064-a001-4affd102e247 b62e372b-3af2-4491-a0df-a025f509e534 5 1 1 I 2025-10-03T16:37:34.807051 04bb4bd8-7c65-472b-a496-77b242a5e488 3b521122-a0d9-4cc2-80a6-a133890deb9c 5 1 1 I 2025-10-03T16:37:34.807051 04bd1ca5-f830-4bcd-8dfd-35c3e2b4fccd b7370d23-7b30-4d64-a8db-15e49b09091d 5 1 1 I 2025-10-03T16:37:34.807051 04e9da41-66ae-4983-bbaa-22648adfd329 4692c510-4cf2-4f19-ac62-144252c97b34 5 1 1 I 2025-10-03T16:37:34.807051 04f8dea5-6023-4886-bfd2-45accdadb6c1 0c83ac5a-7d89-43bc-8208-15e716da7c2b 5 1 1 I 2025-10-03T16:37:34.807051 050e93e7-e8b2-49fa-a3a6-508a02fd76f8 8d66e6e2-1650-4284-bae3-296dfece54da 5 1 1 I 2025-10-03T16:37:

## 4️⃣ Processamento CDC

Carrega arquivos CDC, deduplica e prepara para o merge.

In [0]:
bronze = delta.DeltaTable.forName(spark, f"{catalog}.{schema}.{tablename}")
bronze


In [ ]:
# 📊 ANTES DO MERGE: Captura estatísticas atuais
print("=" * 60)
print("📊 ESTATÍSTICAS ANTES DO MERGE")
print("=" * 60)

# Contagem total antes
count_before = spark.sql(f"SELECT COUNT(*) as total FROM {catalog}.{schema}.{tablename}").collect()[0]['total']
print(f"\n✅ Total de registros ANTES: {count_before:,}")

# Detalhes da tabela antes
details_before = spark.sql(f"DESCRIBE DETAIL {catalog}.{schema}.{tablename}").select("numFiles", "sizeInBytes").collect()[0]
print(f"📁 Arquivos: {details_before['numFiles']}")
print(f"💾 Tamanho: {details_before['sizeInBytes']:,} bytes ({details_before['sizeInBytes'] / (1024*1024):.2f} MB)")

# Última atualização antes
last_update_before = spark.sql(f"""
    SELECT MAX(DtAtualizacao) as ultima_atualizacao 
    FROM {catalog}.{schema}.{tablename}
""").collect()[0]['ultima_atualizacao']
print(f"🕐 Última atualização: {last_update_before}")

print("\n" + "=" * 60)

In [0]:
# Merge CDC na tabela Delta Bronze
print("🔄 Executando merge CDC na tabela Bronze...")

# Verifica se há dados novos para processar
if df_cdc_unique.count() == 0:
    print("⏭️  Nenhum dado CDC novo. Merge não executado.")
    
    # Define variáveis para comparação (sem mudanças)
    count_after = count_before
    details_after = details_before
    last_update_after = last_update_before
    
else:
    bronze = delta.DeltaTable.forName(spark, f"{catalog}.{schema}.{tablename}")
    
    (bronze.alias("b") 
      .merge(df_cdc_unique.alias("d"), f"b.{id_field} = d.{id_field}") 
      .whenMatchedDelete(condition = "d.op = 'D'")           # Delete se op = 'D'
      .whenMatchedUpdateAll(condition = "d.op = 'U'")        # Update se op = 'U'
      .whenNotMatchedInsertAll(condition = "d.op = 'I'")     # Insert se op = 'I'
      .execute()
    )
    
    print("✅ Merge CDC executado com sucesso!")
    
    # 📊 DEPOIS DO MERGE: Captura estatísticas atualizadas
    print("\n" + "=" * 60)
    print("📊 ESTATÍSTICAS DEPOIS DO MERGE")
    print("=" * 60)
    
    # Contagem total depois
    count_after = spark.sql(f"SELECT COUNT(*) as total FROM {catalog}.{schema}.{tablename}").collect()[0]['total']
    print(f"\n✅ Total de registros DEPOIS: {count_after:,}")
    
    # Detalhes da tabela depois
    details_after = spark.sql(f"DESCRIBE DETAIL {catalog}.{schema}.{tablename}").select("numFiles", "sizeInBytes").collect()[0]
    print(f"📁 Arquivos: {details_after['numFiles']}")
    print(f"💾 Tamanho: {details_after['sizeInBytes']:,} bytes ({details_after['sizeInBytes'] / (1024*1024):.2f} MB)")
    
    # Última atualização depois
    last_update_after = spark.sql(f"""
        SELECT MAX(DtAtualizacao) as ultima_atualizacao 
        FROM {catalog}.{schema}.{tablename}
    """).collect()[0]['ultima_atualizacao']
    print(f"🕐 Última atualização: {last_update_after}")

# 🔄 COMPARAÇÃO: Calcula diferenças
print("\n" + "=" * 60)
print("🔄 COMPARAÇÃO: ANTES vs DEPOIS")
print("=" * 60)

diff_records = count_after - count_before
diff_size = details_after['sizeInBytes'] - details_before['sizeInBytes']
diff_files = details_after['numFiles'] - details_before['numFiles']

print(f"\n📊 Diferença de registros: {diff_records:+,} ({'+' if diff_records >= 0 else ''}{(diff_records/count_before*100 if count_before > 0 else 0):.2f}%)")
print(f"💾 Diferença de tamanho: {diff_size:+,} bytes ({diff_size / (1024*1024):+.2f} MB)")
print(f"📁 Diferença de arquivos: {diff_files:+}")

print("\n" + "=" * 60)

## 5️⃣ Merge CDC na Tabela Delta

Aplica as operações de Insert, Update e Delete na camada Bronze.

In [0]:
%sql
select IdTransacao
 from bronze.upcell.transacoes

IdTransacao IdCliente DtCriacao QtdePontos DescSistemaOrigem DtAtualizacao 0000520a-a4e5-4977-b360-17be62fa0f2b 24782f0b-4683-4f35-976a-ea21d6714ba6 2025-09-17 12:28:41.864 1 twitch 2025-10-03T17:05:11.008701 000060e8-aa76-4286-a8d7-f30e6fa47edd 252a0923-3f79-45bb-b664-3040235c6c58 2024-07-23 12:49:49.874 1 twitch 2025-10-03T17:05:11.008701 000095de-3daa-4cfb-a0ae-e7b2c8bc3c9b 30f45a6d-ada5-4a17-8338-710e414eb6c6 2025-09-17 13:38:57.479 1 twitch 2025-10-03T17:05:11.008701 0000c010-a592-46f7-8b0b-6f841bee64ba 65662aff-44d6-4f06-b9d9-07445c6e5943 2025-10-03 12:23:39.779 1 twitch 2025-10-03T17:05:11.008701 0000dfbb-e14e-4ea7-a57f-60236869fffe 5f8fcbe0-6014-43f8-8b83-38cf2f4887b3 2024-02-20 13:21:45.613 1 twitch 2025-10-03T17:05:11.008701 0000e94f-fb76-42b7-82e3-5059b6e40703 3884c92f-a635-4b67-9e5a-97730829cdca 2024-02-05 13:27:18.987 1 twitch 2025-10-03T17:05:11.008701 00017768-81eb-45ae-ad56-f189dd657808 3b878853-34a5-44be-9a8e-05642b853dc6 2025-09-30 12:02:16.448 1 twitch 2025-10-03T17:05:11.008701 00019b46-6b25-47c3-aa8f-f550d7dbcb00 e2624c1c-c8af-4622-94e0-f3470037292f 2024-06-20 19:22:45.600 1 twitch 2025-10-03T17:05:11.008701 0001d503-58d0-4c3e-b0f4-eda1d5f97d06 9aba2685-7c0a-4d1f-8e22-0c47ca0af580 2024-03-18 13:04:21.814 1 twitch 2025-10-03T17:05:11.008701 0001fa55-581a-44e6-8e40-1bb44f82de8e 05de679b-9989-4416-9aa4-20c149999c8d 2024-07-11 13:46:05.759 1 twitch 2025-10-03T17:05:11.008701 000219b4-75c8-4c76-8752-56eaf744bbe0 4fade907-6e0f-4581-a674-aad6622b1b10 2024-08-30 13:43:05.591 1 twitch 2025-10-03T17:05:11.008701 00028d36-4575-4d02-b2a0-bdae1bc83231 9d023e72-c799-40c0-907a-96e023a97959 2024-11-11 12:36:33.625 50 twitch 2025-10-03T17:05:11.008701 00028f94-1cf3-413c-91dd-652dc1a9e161 5f8fcbe0-6014-43f8-8b83-38cf2f4887b3 2024-02-05 11:54:38.711 1 twitch 2025-10-03T17:05:11.008701 00029103-193c-4c63-9cc6-f6f3fbbfbd51 f19aaa00-f337-4174-ba14-a2a39dd6ebbf 2025-09-18 12:02:03.817 1 twitch 2025-10-03T17:05:11.008701 0002df88-1e1f-47b9-8cd4-8f36f21a36c9 b9d0832d-31e7-4031-b548-b060947cde94 2024-08-19 13:43:13.613 1 twitch 2025-10-03T17:05:11.008701 00030a97-75d6-4d58-b0ca-96d4228dc22c 5f8fcbe0-6014-43f8-8b83-38cf2f4887b3 2024-04-20 00:30:59.648 1 twitch 2025-10-03T17:05:11.008701 00030cf7-7a2b-42ab-bbc9-a1642c4cc8c4 700ea785-2faf-4d64-84ea-4e19dc209b56 2025-08-25 13:46:48.572 1 twitch 2025-10-03T17:05:11.008701 000331ee-8fbf-4a2b-a963-6ffd2b86e66a 24782f0b-4683-4f35-976a-ea21d6714ba6 2024-09-04 12:08:52.226 1 twitch 2025-10-03T17:05:11.008701 00033b0f-f658-456c-ab77-e5b40396a2f3 056caf66-d67b-449e-8cba-0bab8aca5949 2025-08-11 12:28:50.404 1 twitch 2025-10-03T17:05:11.008701 00037782-0a3c-4a28-9bd4-564dafec1fca 1856963a-84cb-453e-a139-eb7d8d9b3255 2025-02-19 12:36:18.928 1 twitch 2025-10-03T17:05:11.008701 0003b91b-a75a-46e5-8af6-fcc890b98952 5877cf53-bde0-4bfa-b61b-0a09e5dd5147 2024-01-30 13:17:36.457 1 twitch 2025-10-03T17:05:11.008701 00045cfe-f131-4505-ba34-d89f099a8625 69e9a7c3-6f64-430f-96ee-eb1548eb6aad 2024-02-05 13:35:41.807 1 twitch 2025-10-03T17:05:11.008701 0004bd85-fe2c-4b39-a7f0-1a05b009011a da98830d-a2d1-4c15-801d-dd58ef7713fb 2025-10-01 13:37:39.603 1 twitch 2025-10-03T17:05:11.008701 0004da1b-ab20-4460-9106-3aeca2844789 5f8fcbe0-6014-43f8-8b83-38cf2f4887b3 2025-09-02 12:00:52.769 1 twitch 2025-10-03T17:05:11.008701 0005255f-3ab1-4052-a0d5-0f71a87e492e d6ae3f9a-f285-4a55-9888-9e950a775b76 2025-03-18 11:10:11.890 1 twitch 2025-10-03T17:05:11.008701 0005855d-2c33-4bfd-85fe-2c7ffaf73151 f5719706-915b-4bb1-b9be-c4acb3bd7837 2025-07-16 12:05:28.007 50 twitch 2025-10-03T17:05:11.008701 0005df42-fa29-418e-8da8-cf60ed680a28 c4c318f5-16b8-4c4f-b830-56d6e79f458e 2024-11-19 11:40:09.911 1 twitch 2025-10-03T17:05:11.008701 000649f4-446e-4c61-b527-50db534ab6fb 8d86f053-91ab-44ed-aeb8-74cad60760b8 2025-04-24 13:13:21.114 1 twitch 2025-10-03T17:05:11.008701 00068684-c433-45e1-ae95-a6b94cbeb514 961622c3-3c29-4fa1-88d2-4f408d6d6ebb 2024-08-09 13:14:40.064 1 twitch 2025-10-03T17:05:11.008701 00068e23-5b1e-432a-83df-8a5d11e495a6 

In [ ]:
# Validação 1: Contagem total de registros
total = spark.sql(f"SELECT COUNT(*) as total FROM {catalog}.{schema}.{tablename}").collect()[0]['total']
print(f"📊 Total de registros na tabela Bronze: {total:,}")

# Validação 2: Verificar se DtAtualizacao está presente
sample = spark.sql(f"SELECT * FROM {catalog}.{schema}.{tablename} LIMIT 5")
print(f"\n✅ Colunas da tabela: {sample.columns}")
sample.display()

In [ ]:
# Validação 3: Verificar histórico de versões Delta
print("📜 Histórico de versões da tabela Delta:\n")
spark.sql(f"DESCRIBE HISTORY {catalog}.{schema}.{tablename}").select(
    "version", 
    "timestamp", 
    "operation", 
    "operationMetrics"
).display()

In [ ]:
-- Validação 4: Análise de dados por DtAtualizacao
SELECT 
    DATE(DtAtualizacao) as data_atualizacao,
    COUNT(*) as total_registros,
    MIN(DtAtualizacao) as primeira_atualizacao,
    MAX(DtAtualizacao) as ultima_atualizacao
FROM bronze.upcell.transacao_produto
GROUP BY DATE(DtAtualizacao)
ORDER BY data_atualizacao DESC

### 🎯 Próximos Passos:

1. **Executar para outras tabelas**: Altere a variável `tablename` para processar:
   - `clientes`
   - `produtos`
   - `transacoes`

2. **Agendar execução**: Configure um Job no Databricks para rodar periodicamente

3. **Otimizar tabela**: Execute `OPTIMIZE` e `VACUUM` periodicamente:
   ```sql
   OPTIMIZE bronze.upcell.transacao_produto;
   VACUUM bronze.upcell.transacao_produto RETAIN 168 HOURS;
   ```

4. **Monitorar**: Use `DESCRIBE HISTORY` para acompanhar versões

## 6️⃣ Validação Final

Consulta a tabela Bronze para validar os dados.

---

## 📚 Referência: Operações CDC

| Operação | Código | Descrição | Ação no Merge |
|----------|--------|-----------|---------------|
| **Insert** | `I` | Novo registro | `whenNotMatchedInsertAll()` |
| **Update** | `U` | Registro atualizado | `whenMatchedUpdateAll()` |
| **Delete** | `D` | Registro deletado | `whenMatchedDelete()` |

### 🔍 Como Funciona o QUALIFY:

```sql
QUALIFY ROW_NUMBER() OVER(PARTITION BY {id_field} ORDER BY {timefield} DESC) = 1
```

- **PARTITION BY**: Agrupa por chave primária
- **ORDER BY DESC**: Ordena pelo timestamp (mais recente primeiro)
- **ROW_NUMBER() = 1**: Pega apenas o registro mais recente de cada chave

### ✅ Checklist de Validação:

- [ ] Full-load executado com sucesso
- [ ] CDC processado sem erros
- [ ] Merge aplicado corretamente
- [ ] Contagem de registros confere
- [ ] Coluna `DtAtualizacao` presente em todos os registros